# Matrix Generation

In [1]:
import sys
sys.path.append("../")
from Recipe import Recipe, Ingredient, RecipeGraph

import settings
import db.db_settings as db_settings
from db.database_connection import DatabaseConnection

import random

import itertools

import numpy as np

In [2]:
DatabaseConnection(db_settings.db_host,
                   db_settings.db_port,
                   db_settings.db_user,
                   db_settings.db_pw,
                   db_settings.db_db,
                   db_settings.db_charset)

In [3]:
%time ids = DatabaseConnection.global_single_query("select id from recipes")

CPU times: user 8.56 s, sys: 924 ms, total: 9.48 s
Wall time: 9.5 s


In [4]:
import AdjacencyMatrix

* create Adjacency Matrix

In [11]:
def add_entries_from_rec_state(rec_state, m_act, m_mix, m_base_act, m_base_mix):
    mix_m, mix_label = rec_state.get_mixing_matrix()
    act_m, act_a, act_i = rec_state.get_action_matrix()

    # create list of tuples: [action, ingredient]
    seen_actions = np.array(list(itertools.product(act_a,act_i))).reshape((len(act_a), len(act_i), 2))

    # create list of tuples [ingredient, ingredient]
    seen_mixes = np.array(list(itertools.product(mix_label,mix_label))).reshape((len(mix_label), len(mix_label), 2))

    seen_actions = seen_actions[act_m == 1]
    seen_mixes = seen_mixes[mix_m == 1]

    seen_actions = set([tuple(x) for x in seen_actions.tolist()])
    seen_mixes = set([tuple(x) for x in seen_mixes.tolist()])
    
    seen_base_actions = set()
    seen_base_mixes = set()
    
    for act, ing in seen_actions:
        m_act.add_entry(act, ing.to_json(), 1)
        if (act, ing._base_ingredient) not in seen_base_actions:
            seen_base_actions.add((act, ing._base_ingredient))
            m_base_act.add_entry(act, ing._base_ingredient, 1)
    
    for x,y in seen_mixes:
        xj = x.to_json()
        yj = y.to_json()
        if xj < yj:
            m_mix.add_entry(xj,yj,1)
            if (x._base_ingredient, y._base_ingredient) not in seen_base_mixes:
                seen_base_mixes.add((x._base_ingredient, y._base_ingredient))
                m_base_mix.add_entry(x._base_ingredient, y._base_ingredient, 1)


In [12]:
m_act = AdjacencyMatrix.adj_matrix()
m_mix = AdjacencyMatrix.adj_matrix(True)
m_base_act = AdjacencyMatrix.adj_matrix()
m_base_mix = AdjacencyMatrix.adj_matrix(True)

In [13]:
%%time
for i in range(100000):
    id = random.choice(ids)['id']
    rec = Recipe(id)
    #rec.display_recipe()
    ing = rec.extract_ingredients()
    if len(ing) == 0:
        print(f"warning: recipe {id} has no ingredient! skipping it")
        continue
    rec.apply_instructions(debug=False)
    add_entries_from_rec_state(rec._recipe_state, m_act, m_mix, m_base_act, m_base_mix)

CPU times: user 2h 17min 59s, sys: 41 s, total: 2h 18min 40s
Wall time: 2h 20min 22s


In [14]:
i

99999

In [31]:
import dill

In [32]:
dill.dump(m_act, file=open("m_act_raw.dill", 'wb'))
dill.dump(m_mix, file=open("m_mix_raw.dill", 'wb'))
dill.dump(m_base_act, file=open("m_base_act_raw.dill", 'wb'))
dill.dump(m_base_mix, file=open("m_base_mix_raw.dill", 'wb'))

In [37]:
m_act.apply_threshold(10)
m_mix.apply_threshold(10)
m_base_act.apply_threshold(50)
m_base_mix.apply_threshold(50)

In [33]:
c_mix = m_mix.get_csr()
c_act = m_act.get_csr()
c_base_mix = m_base_mix.get_csr()
c_base_act = m_base_act.get_csr()

In [39]:
m_mix.compile()
m_act.compile()
m_base_mix.compile()
m_base_act.compile()


In [43]:
dill.dump(m_act, file=open("m_act.dill", 'wb'))
dill.dump(m_mix, file=open("m_mix.dill", 'wb'))
dill.dump(m_base_act, file=open("m_base_act.dill", 'wb'))
dill.dump(m_base_mix, file=open("m_base_mix.dill", 'wb'))

In [34]:
print(c_act.shape, c_mix.shape)
print(len(c_act.nonzero()[0]),len(c_mix.nonzero()[0]))
print(c_base_act.shape, c_base_mix.shape)
print(len(c_base_act.nonzero()[0]),len(c_base_mix.nonzero()[0]))

(65, 384445) (433582, 433582)
749954 4526723
(65, 17483) (22059, 22059)
114758 590425


In [35]:
print(c_act.shape, c_mix.shape)
print(len(c_act.nonzero()[0]),len(c_mix.nonzero()[0]))

(65, 384445) (433582, 433582)
749954 4526723


In [36]:
np.sum(c_act.toarray() > 1)

171424

array([[1, 1, 0, ..., 0, 0, 0],
       [0, 0, 1, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ...,
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]], dtype=int64)

* values after 100:
```
(53, 1498) (1620, 1620)
1982 6489
```

* after 1000:
```
(60, 9855) (10946, 10946)
15446 59943
```

* after 10000:
```
(65, 65235) (72448, 72448)
114808 546217
```